In [1]:
%load_ext autoreload
%autoreload 2

from scripts.experiments.main_experiment import MainExperiment
from hydra.initialize import initialize
from hydra.compose import compose

e = MainExperiment(None)
with initialize(version_base=None, config_path="config"):
    e.config = compose(config_name=e.experiment_name)

In [2]:
e.specification()

[RunDescriptor(run_fun=<scripts.run_generative_rendering.RunGenerativeRendering object at 0x7fab025d4970>, config={'run': {'wandb': True, 'instant_exit': False, 'download_artifacts': False, 'name': None, 'group': None, 'tags': []}, 'prompt': 'Realistic Deadpool, Simple White Background', 'animation': {'n_frames': 20, 'artifact_tag': 'handstand:latest'}, 'generative_rendering': {'attend_to_self_kv': True, 'do_pre_attn_injection': True, 'do_post_attn_injection': True, 'feature_blend_alpha': 1.0, 'mean_features_weight': 0.5, 'chunk_size': 5, 'num_keyframes': 10, 'num_inference_steps': 10, 'guidance_scale': 7.5, 'controlnet_conditioning_scale': 1.0, 'module_paths': ['up_blocks.1.attentions.0.transformer_blocks.0.attn1', 'up_blocks.1.attentions.1.transformer_blocks.0.attn1', 'up_blocks.1.attentions.2.transformer_blocks.0.attn1', 'up_blocks.2.attentions.0.transformer_blocks.0.attn1', 'up_blocks.2.attentions.1.transformer_blocks.0.attn1', 'up_blocks.2.attentions.2.transformer_blocks.0.attn1',

In [3]:
e.execute_runs(dry_run=True)

would execute 3 runs


In [46]:
from text3d2video.artifacts.anim_artifact import AnimationArtifact
from text3d2video.rendering import render_depth_map
from text3d2video.utilities.video_util import pil_frames_to_clip
import wandb_util.wandb_util as wbu
from omegaconf import OmegaConf

r = e.get_logged_runs()[0]

n_frames = OmegaConf.create(r.config).animation.n_frames
anim = wbu.first_used_artifact_of_type(r, 'animation')
anim = AnimationArtifact.from_wandb_artifact(anim)

frame_indices = anim.frame_indices(n_frames)
cams, meshes = anim.load_frames(frame_indices)
depth_frames = render_depth_map(meshes, cams)

depth_vid = pil_frames_to_clip(depth_frames, fps=10)

In [47]:
e.video_comparison(with_labels=True).ipython_display()

Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4
